Binary Classification Notebook

Create user and grant permission to create model

In [0]:
create user demouser with password '<yourpassword>';

GRANT CREATE MODEL TO demouser;

Create schema and table

In [0]:
CREATE SCHEMA DEMO_ML; 
CREATE TABLE demo_ml.customer_activity (
state varchar(2), 
account_length int, 
area_code int,
phone varchar(8), 
intl_plan varchar(3), 
vMail_plan varchar(3),
vMail_message int, 
day_mins float, 
day_calls int, 
day_charge float,
total_charge float,
eve_mins float, 
eve_calls int, 
eve_charge float, 
night_mins float,
night_calls int, 
night_charge float, 
intl_mins float, 
intl_calls int,
intl_charge float, 
cust_serv_calls int, 
churn varchar(6),
record_date date);

Load data into the table

In [0]:
COPY DEMO_ML.customer_activity 
FROM 's3://redshift-downloads/redshift-ml/customer_activity/' 
IAM_ROLE default delimiter ',' IGNOREHEADER 1  
region 'us-east-1';

Create model - replace <redshiftml-<your-account-id>'> with your S3 bucket

In [0]:
GRANT SELECT on demo_ml.customer_activity TO demouser;
GRANT CREATE, USAGE ON SCHEMA demo_ml TO demouser;
CREATE MODEL demo_ml.customer_churn_model
FROM (SELECT state,
             area_code,
             total_charge/account_length AS average_daily_spend, 
             cust_serv_calls/account_length AS average_daily_cases,
             churn 
      FROM demo_ml.customer_activity
         WHERE record_date < '2020-01-01' 

     )
TARGET churn
FUNCTION predict_customer_churn
IAM_ROLE default
SETTINGS (
  S3_BUCKET 'redshiftml-<your-account-id>'
)
;

check status of model

In [0]:
SHOW MODEL demo_ml.customer_churn_model;

Evaluate your model performance

In [0]:
WITH infer_data AS (
  SELECT area_code ||phone  accountid, churn,
    demo_ml.predict_customer_churn( 
          state,
          area_code, 
          total_charge/account_length , 
          cust_serv_calls/account_length ) AS predicted
  FROM demo_ml.customer_activity
WHERE record_date <  '2020-01-01'

)
SELECT *  FROM infer_data where churn!=predicted;

Evaluate your model performance with prediction probabilities

In [0]:
WITH infer_data AS (
  SELECT area_code ||phone  accountid, churn,
    demo_ml.predict_customer_churn_prob( 
          state,
          area_code, 
          total_charge/account_length , 
          cust_serv_calls/account_length ) AS predicted
  FROM demo_ml.customer_activity
WHERE record_date <  '2020-01-01'

)
SELECT *  FROM infer_data where churn!=predicted;

Invoke your model for inference

In [0]:
SELECT area_code ||phone  accountid, 
       demo_ml.predict_customer_churn( 
          state,
          area_code, 
          total_charge/account_length , 
          cust_serv_calls/account_length )
          AS "predictedActive"
FROM demo_ml.customer_activity
WHERE area_code='408' and record_date > '2020-01-01';

Invoke your Model for inference with probabilities

In [0]:
SELECT accountid, predictedActive.labels[0] as
predictedActive,predictedActive.probabilities[0]
FROM (SELECT area_code ||phone accountid, predict_customer_churn_prob(
state,
area_code,
total_charge/account_length ,
cust_serv_calls/account_length ) AS predictedActive
FROM customer_activity
WHERE area_code='408' and record_date > '2020-01-01'
);

Check prediction probabilities count on all inference data

In [0]:
Select cast(prediction.probabilities[0] as decimal(4,1)) as probabilities, count(*)
from (select
area_code ||phone accountid,
predict_customer_churn_prob(
state,
area_code,
total_charge/account_length ,
cust_serv_calls/account_length ) as prediction
from customer_activity
)t1
group by 1
order by 1 desc;